In [1]:
import bs4
import requests
import os
import re
import os
import datetime
import json

In [2]:
# download main page to get download links
page = requests.get('https://catalog.unc.edu/courses/')
f = open('/Users/aniruddhdoki/Library/Mobile Documents/com~apple~CloudDocs/school/NCSSM/senior year/semester 2/cs4280 advanced java/cs4280-final-project/data/course pages/courses.html', "wb")
f.write(page.content)
f.close()
headers = page.headers
print(headers)

{'Date': 'Wed, 11 May 2022 02:42:22 GMT', 'Server': 'Apache/2.4.6 (CentOS) OpenSSL/1.0.2k-fips', 'Last-Modified': 'Tue, 25 Jan 2022 21:53:40 GMT', 'ETag': '"b143-5d66f1e3f1865"', 'Accept-Ranges': 'bytes', 'Content-Length': '45379', 'X-Frame-Options': 'SAMEORIGIN', 'Keep-Alive': 'timeout=5, max=100', 'Connection': 'Keep-Alive', 'Content-Type': 'text/html; charset=UTF-8'}


In [3]:
# get links to all course pages
file = open('/Users/aniruddhdoki/Library/Mobile Documents/com~apple~CloudDocs/school/NCSSM/senior year/semester 2/cs4280 advanced java/cs4280-final-project/data/course pages/courses.html', 'r')
html = bs4.BeautifulSoup(file, 'html5lib')
file.close()

categories = []
links = html.find('ul', {'id': '/courses/'}).find_all('a')
links = list(links)
for link in links:
  categories.append(link['href'])

categoryLinks = []
for category in categories:
  categoryLinks.append(f'https://catalog.unc.edu{category}')

In [4]:
# download the category pages
if len(categoryLinks) == len(categories):
  for i in range(len(categories)):
    page = requests.get(categoryLinks[i])
    f = open(f'/Users/aniruddhdoki/Library/Mobile Documents/com~apple~CloudDocs/school/NCSSM/senior year/semester 2/cs4280 advanced java/cs4280-final-project/data/course pages/{categories[i][:-1]}.html', "wb")
    f.write(page.content)
    f.close()

In [50]:
# scrape course catalog
directory = '/Users/aniruddhdoki/Library/Mobile Documents/com~apple~CloudDocs/school/NCSSM/senior year/semester 2/cs4280 advanced java/cs4280-final-project/data/course pages/courses'
output = {}
for file in os.listdir(directory):
  f = os.path.join(directory, file)
  if os.path.isfile(f):
    print(f'\n{datetime.datetime.now()} current file: {file}')
    page = open(f, 'r')
    html = bs4.BeautifulSoup(page, 'html5lib')
    page.close()
    courses = list(html.findAll('div', {'class': 'courseblock'}))
    for course in courses:
      try:
        rawTitle = course.findAll('p', {'class': 'courseblocktitle'})
        rawTitle = rawTitle[0].stripped_strings
        for title in rawTitle:
          # get raw title text and clean it
          title = repr(title)
          if 'xa0' in title:
            title = title.replace('\\xa0', ' ')
          title = re.sub(r'(\\n)', ' ', title)
          title = re.sub('\s+', ' ', title)
          title = title.split('.')

          # get course code
          courseCode = title[0].strip().split('\'')[1].replace(' ', '')

          # get course title
          courseTitle = title[1].strip()

          # get number of credit hours awarded
          creditHoursAwarded = title[2].strip()
        
        # get raw text of description and clean it
        rawDesc = course.findAll('p', {'class': 'courseblockdesc'})
        rawDesc = rawDesc[0].get_text()
        rawDesc = re.sub(r'(\\n)', ' ', rawDesc)
        rawDesc = re.sub('\s+', ' ', rawDesc)

        # get course description
        try:
          if 'Gen Ed:' in rawDesc:
            courseDesc = re.split(r'Gen Ed:', rawDesc)
            courseDesc = courseDesc[0].strip()
        except:
          print(f'no course description found for {courseCode}')
          courseDesc = 'none'

        # get making connections requirement info
        try:
          if 'Repeat rules:' in rawDesc:
            makingConnections = re.split(r'Gen Ed:(.+?\.)', rawDesc)
            makingConnections = makingConnections[1].strip()
        except:
          print(f'no making connections information found for {courseCode}')
          makingConnections = 'none'

        # get repeat rules:
        try:
          if 'Repeat rules:' in rawDesc:
            repeatRules = re.split(r'Repeat rules:(.+?)Grading', rawDesc)
            repeatRules = repeatRules[1].strip()
        except:
          print(f'no repeat rules found for {courseCode}')
          repeatRules = 'none'
      
        # get grading status rules 
        try:
          if 'Grading status:' in rawDesc:
            gradingStatus = re.split(r'Grading status:(.+)?Same as', rawDesc)
            gradingStatus = gradingStatus[1].strip()
        except:
          print(f'no repeat rules found for {courseCode}')
          gradingStatus = 'none'

        # get same as info
        try:
          if 'Same as:' in rawDesc:
            sameAs = re.split(r'Same as:(.+)?\.', rawDesc)
            sameAs = sameAs[1].strip()
        except:
          print(f'no same as information found for {courseCode}')
          sameAs = 'none'

        data = {
          'category': file,
          'course code': courseCode,
          'course title': courseTitle,
          'credit hours awarded': creditHoursAwarded,
          'description': courseDesc,
          'making connections requirement': makingConnections,
          'ideas in action requirement': '',
          'repeat rules': repeatRules,
          'grading status': gradingStatus,
          'same as': sameAs,
        }
        # print(courseCode)
        # print(data)
        output[courseCode] = data
      except:
        print(f'an unknown error occured with {file} at {datetime.datetime.now()}')
print(output)


2022-05-10 23:33:25.964222 current file: arch.html
no repeat rules found for ARCH393
no making connections information found for ARCH395
no repeat rules found for ARCH395
no making connections information found for ARCH396
no repeat rules found for ARCH396
no repeat rules found for ARCH691H
no repeat rules found for ARCH692H

2022-05-10 23:33:26.053308 current file: engl.html
no repeat rules found for ENGL50
no repeat rules found for ENGL52
no repeat rules found for ENGL53
no repeat rules found for ENGL54
an unknown error occured with engl.html at 2022-05-10 23:33:26.484347
no repeat rules found for ENGL57
no repeat rules found for ENGL58
no repeat rules found for ENGL59
no repeat rules found for ENGL63
no repeat rules found for ENGL66
no repeat rules found for ENGL69
no repeat rules found for ENGL70
no repeat rules found for ENGL71
no repeat rules found for ENGL72
no repeat rules found for ENGL73
no repeat rules found for ENGL74
no repeat rules found for ENGL75
no repeat rules found 

In [51]:
# get the ideas in action information into the data
directory = '/Users/aniruddhdoki/Library/Mobile Documents/com~apple~CloudDocs/school/NCSSM/senior year/semester 2/cs4280 advanced java/cs4280-final-project/data/course pages/ideas in action'
for file in os.listdir(directory):
  if file != '.DS_Store':  
    f = os.path.join(directory, file)
    if os.path.isfile(f):
      print(f'\n{datetime.datetime.now()} current file: {file}')
      page = open(f, 'r')
      html = bs4.BeautifulSoup(page, 'html5lib')
      page.close()

    # table = html.find('tbody', {'class': 'wpv-loop js-wpv-loop'})
    # tableRows = list(table.children)
    # for row in tableRows:
    #   print(row)
    #   row
    # # print(tableRows)

    for row in html.select('tbody tr'):
      tds = [td.text for td in row.findAll('td')]
      try:
        possibilities = [tds[0]]
        possibilities.extend(tds[3].split(','))
        possiblities = [possibility.replace(' ', '').strip() for possibility in possibilities]
        for possibility in possibilities:
          if possibility in output:
            data = output[possibility]
            data['ideas in action requirement'] = tds[2]
            output[possibility] = data
          else:
            data = output[possibility]
            data['ideas in action requirement'] = 'none'
            output[possibility] = data

        print(tds[3].split(','))
      except:
        print(f'unknown error in {file}')

# print(output)
    


2022-05-10 23:33:47.141222 current file: 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html
unknown error in 23.html


In [52]:
# export data to json
jsonPath = r'/Users/aniruddhdoki/Library/Mobile Documents/com~apple~CloudDocs/school/NCSSM/senior year/semester 2/cs4280 advanced java/cs4280-final-project/data/data.json'

if os.path.exists(jsonPath):
  os.remove(jsonPath)
with open(jsonPath, "w") as outfile:
  json.dump(output, outfile)